In [1]:
import requests
import pandas as pd
import duckdb
import toml
import datetime
from datetime import datetime as dt
import time
import json
from ast import literal_eval



In [1]:
# A pipeline coded the good old way

# Let's build a function for the football data source. 
# Its arguments will be: 
#   endpoint, 
#   params (I'll start with data from the 2023/2024 season),   
#   column names (list)
# That way we can call the function without copy pasting the code again and again for each endpoint

import requests
import pandas as pd
import duckdb
import toml
import datetime
from datetime import datetime as dt 
import time
import json
from ast import literal_eval

# /?dateFrom=2022-01-01
# /?dateTo=2022-01-10

def extract_load_football_data(
        endpoint = None,
        column_names = None,
        **params # Note: Arbitrary keyword arguments are dictionaries
):
    
    # Step 0: import API credentials
    secrets=toml.load("C:/Users/mbmbm/matbx-data/sports-db-project/sports_db_pipeline/secrets.toml")
    request_header=secrets['source']['football_data']['request_header']
    api_key=secrets['source']['football_data']['api_key']

    # Step 1: Define request URL
    # If there are no parameters passed to the function (meaning: params is an empty dictionary), take the whole endpoint
    if params == {}: 
        url = f'https://api.football-data.org/v4/{endpoint}'
    else:
        url = f'https://api.football-data.org/v4/{endpoint}/?dateFrom={params['start_date']}&dateTo={params['end_date']}' # Note: we access each params' key's value as in any dictionary

    # Step 2: Make the GET request to the API, using a header to authenticate through API key
    response = requests.get(url, headers={request_header:api_key})

    # Step 3: Convert the JSON returned to a pandas DataFrame
    endpoint_df = pd.DataFrame(
        data=response.json()[f'{endpoint}'],
        columns = column_names
    )

    # DuckDB documentation to load data from pandas: https://duckdb.org/docs/stable/guides/python/import_pandas.html
    # Here, the "with" structure is a context manager that enables to close the connection (created on the just above line) automatically
    # Note that we prefix the table name with "raw", which specifies the schema we want to populate
    database_path = "C:/Users/mbmbm/matbx-data/sports-db-project/duckdb-databases/sports_db.duckdb"
    try:
        with duckdb.connect(database_path) as con:
            con.sql(f"CREATE OR REPLACE TABLE raw.football_data__{endpoint} AS SELECT * FROM endpoint_df")
        message="Successfully pushed dataframe to DuckDB"
    except:
        message="Error, couldn't load data into DuckDB"

    return(message)

In [2]:
# Calling pipelines

# Competitions
extract_load_football_data(
    endpoint='competitions', 
    column_names=[
        'id', 
        'area', 
        'name', 
        'code', 
        'type', 
        'currentSeason', 
        'lastUpdated'
    ]
)

# Areas
extract_load_football_data(
    endpoint='areas', 
    column_names=[ 
        "id",
        "name",
        "countryCode",
        "flag",
        "parentAreaId",
        "parentArea"
    ]
)

# Teams
extract_load_football_data(
    endpoint='teams', 
    column_names=[ 
        "id",
        "name",
        "shortName",
        "tla",
        "address",
        "website",
        "founded",
        "clubColors",
        "venue",
        "runningCompetitions",
        "coach",
        "marketValue",
        "squad",
        "staff",
        "lastUpdated"
    ]
)

'Successfully pushed dataframe to DuckDB'

In [2]:
# Extract matches

time.sleep(100)
# Step 0: import API credentials
secrets=toml.load("C:/Users/mbmbm/matbx-data/sports-db-project/sports_db_pipeline/secrets.toml")
request_header=secrets['source']['football_data']['request_header']
api_key=secrets['source']['football_data']['api_key']

# Seems like data is available from 2024-06-01
# Also, specified period cannot exceed 10 days
# What to do in this section: Build 10-days periods and extract matches for each and every one of them

# Step 1: Build 10-days periods 

# Intialization
start_date = dt.strptime("2024-08-01", "%Y-%m-%d") # From around the start of the major leagues' 2024/25 season
end_date = dt.now() + pd.DateOffset(months=12) # Add 12 months to ensure we capture all matches in a season. 
date_iterator = start_date
periods = []

while date_iterator <= end_date:
    start_date = date_iterator
    date_iterator = date_iterator + datetime.timedelta(days=10)
    periods.append({"start_date":start_date, "end_date":date_iterator})

ten_days_periods = pd.DataFrame(periods)

# Step 2: Pull data from API for each 10-days period to get all matches for the current season
# It is clearly specified in the documentation that the max number of requests per minute is 10. We set a 60 second timer after each 10 requests.

i = 0 # Setting a counter (i) to rest 60 seconds after 10 requests
matches_list = [] # Setting an empty list to store API calls results

for index, period in ten_days_periods.iterrows():
    i = i + 1
    period_start_date = dt.strftime(period['start_date'], "%Y-%m-%d") # Format for inserting the date in the request's url
    period_end_date = dt.strftime(period['end_date'], "%Y-%m-%d") # Note that the end_date is also the first_date of the next period. This should lead to duplication in the API requests, but will not because the "dateTo" filter of the API is exclusive
    
    # Making the actual requests
    url = f"https://api.football-data.org/v4/matches/?dateFrom={period_start_date}&dateTo={period_end_date}"
    print(url)
    print(requests.get(url, headers={request_header:api_key}).json())
    try:
        response = requests.get(url, headers={request_header:api_key}).json()['matches'] # This is a list
    except:
        print("Failed at api request")
    matches_list.append(response)
    
    if i%5==0: time.sleep(60) # Stop the program for 60 second each 5 requests. Why 5? Because it feels like the "10 requests per minute" are too much for the API


https://api.football-data.org/v4/matches/?dateFrom=2024-08-01&dateTo=2024-08-11
{'filters': {'dateFrom': '2024-08-01', 'dateTo': '2024-08-11', 'permission': 'TIER_ONE'}, 'resultSet': {'count': 31, 'competitions': 'BSA,DED,ELC,PPL', 'first': '2024-08-03', 'last': '2024-08-10', 'played': 31}, 'matches': [{'area': {'id': 2032, 'name': 'Brazil', 'code': 'BRA', 'flag': 'https://crests.football-data.org/764.svg'}, 'competition': {'id': 2013, 'name': 'Campeonato Brasileiro Série A', 'code': 'BSA', 'type': 'LEAGUE', 'emblem': 'https://crests.football-data.org/bsa.png'}, 'season': {'id': 2257, 'startDate': '2024-04-13', 'endDate': '2024-12-08', 'currentMatchday': 38, 'winner': None}, 'id': 493962, 'utcDate': '2024-08-03T19:00:00Z', 'status': 'FINISHED', 'matchday': 21, 'stage': 'REGULAR_SEASON', 'group': None, 'lastUpdated': '2024-12-22T20:20:40Z', 'homeTeam': {'id': 1782, 'name': 'EC Vitória', 'shortName': 'Vitória', 'tla': 'VIT', 'crest': 'https://crests.football-data.org/1782.png'}, 'awayTea

In [4]:
# Now, the only thing we still need to do is concatenate the requests outputs together (equivalent of UNION ALL in SQL)
# First, let's get all the columns we will have in the final matches DataFrame
matches_columns = list(pd.DataFrame(matches_list[0]).columns)

# Creating an empty DataFrame
matches_df = pd.DataFrame(columns = matches_columns)

# Now, each element in matches_list is a list of dictionaries. We convert each element to a DataFrame, and concatenate it to the matches_df

for item in matches_list:
    matches_df = pd.concat([matches_df, pd.DataFrame(item)])

matches_df.reset_index(inplace=True, drop=True)
matches_df['winner'] = matches_df['score'].map(lambda x: x['winner']) # Accessing each 'winner' item of each row. Did so because matches_df['score']['winner'] doesn't work cause df['score'] returns a series of dicts. The series per say doesn't have a 'winner' key.
matches_df['duration'] = matches_df['score'].map(lambda x: x['duration'])
matches_df['full_time'] = matches_df['score'].map(lambda x: x['fullTime'])
matches_df['half_time'] = matches_df['score'].map(lambda x: x['halfTime'])
matches_df = matches_df.drop(columns='score')

database_path = "C:/Users/mbmbm/matbx-data/sports-db-project/duckdb-databases/sports_db.duckdb"
# # And we finally have our matches source table, ready to be pushed to our raw DuckDB database
with duckdb.connect(database_path) as con:
    con.sql("CREATE OR REPLACE TABLE raw.football_data__matches AS SELECT * FROM matches_df")

In [3]:
# Extract teams
# The football-data.org API free plan grants us access to the 12 major football leagues.
# Therefore, we can only access the teams data for these 12 leagues' teams
# Strategy : iterate through each league ID and extract the teams that belong to them.

# Since we only have 12 leagues, I manually listed them below:
major_league_ids = [
    2002,  # Bundesliga
    2013,  # Campeonato Brasileiro Série A
    2016,  # Championship
    2152,  # Copa Libertadores
    2003,  # Eredivisie
    2018,  # European Championship
    2015,  # Ligue 1
    2021,  # Premier League
    2017,  # Primeira Liga
    2014,  # Primera Division
    2019,  # Serie A
    2001   # UEFA Champions League
]

# Step 0: import API credentials
secrets=toml.load("C:/Users/mbmbm/matbx-data/sports-db-project/sports_db_pipeline/secrets.toml")
request_header=secrets['source']['football_data']['request_header']
api_key=secrets['source']['football_data']['api_key']

i = 0 # Set a count to deal with the limit of 10 requests per minute
#####################################################################################################################
# (Notebook only)
full_df = pd.DataFrame() # Creating an empty DataFrame to prevent from working with an already existing one 
#####################################################################################################################

# Step 1: Set up the loop

# Note that there is a slight tweak here. European competitions' seasons overlap two calendar year. So, season 2024 of Ligue 1 is actually season 2024/2025
# On the contrary, in South America, competitions start around the beginning of the year and end around the end of the year. So the 2024 season is really the 2024.
# For this project's sake, we want to be able to analyze the current season.
# This means season 2024 in Europe and season 2025 in South America. 
# The extraction needs to take this point into account.

for id in major_league_ids:
    # Extracting season 2025 of South American competitions
    if id in (2013, 2152):
        url = f"http://api.football-data.org/v4/competitions/{id}/teams?season=2025" 
    # Extracting season 2024 of European competitions
    else: 
        url = f"http://api.football-data.org/v4/competitions/{id}/teams?season=2024" # Extracting season 2024 of European competitions
    response = requests.get(url, headers={request_header:api_key}).json()
    
    i = i + 1
    
    #####################################################################################################################
    # (Notebook only)
    print()
    print(f"MAJOR LEAGUE ID : {id}")
    print(f"ITERATION N°{i}")
    print(response)
    print(response['teams'])
    #####################################################################################################################
    
    # Step 2: Create the DataFrame
    df = pd.DataFrame(response['teams'])

    # Step 2a: Add season and competition  
    # We add a few key information to the teams that are not contained in the 'teams' json's item: competition, season.
    # I don't necessarilly understand why, but to add json columns to a DataFrame, we need to pass it to the json.dumps() function.
    # For better understanding of the data structure, don't hesitate to print the "response" variable
    df['competition'] = json.dumps(response['competition']) 

    # Remove "winner" item with Dict Comprehension. Its null values make literal_eval() below crash
    season_without_winner = {k: v for k, v in response['season'].items() if k != "winner"}
    df['season'] = json.dumps(season_without_winner)

    # Step 2b: Handle string format of these columns
    # We will convert the "season" and "competition" columns values into dicts (the literal_eval() function does so). This will enable DuckDB to treat it as a STRUCT. Otherwise, we would end up with a VARCHAR column containing JSON. Doing this step in Python will make it easier to deal with the column in DBT further down the process.
    df['competition'] = df['competition'].apply(lambda x: literal_eval(x))
    df['season'] = df['season'].apply(lambda x: literal_eval(x)) 
    
    # Step 3: Concatenate the current DataFrame with the previous one
    # On the first iteration, the 'try' will fail, and create a first version of the 'full_df' (e.g. the df that stores all previous iterations)
    try:
        full_df = pd.concat([full_df, df])
    except:
        full_df = df

    # Set timer after 10 requests    
    if i%10 == 0: time.sleep(70)    

teams_df = full_df
teams_df.reset_index(inplace=True, drop=True)

# And we finally have our teams source table, ready to be pushed to our raw DuckDB database
database_path = "C:/Users/mbmbm/matbx-data/sports-db-project/duckdb-databases/sports_db.duckdb"
with duckdb.connect(database_path) as con:
    con.sql("CREATE OR REPLACE TABLE raw.football_data__teams AS SELECT * FROM teams_df")


MAJOR LEAGUE ID : 2002
ITERATION N°1
{'count': 18, 'filters': {'season': 2024}, 'competition': {'id': 2002, 'name': 'Bundesliga', 'code': 'BL1', 'type': 'LEAGUE', 'emblem': 'https://crests.football-data.org/BL1.png'}, 'season': {'id': 2308, 'startDate': '2024-08-23', 'endDate': '2025-05-17', 'currentMatchday': 29, 'winner': None}, 'teams': [{'area': {'id': 2088, 'name': 'Germany', 'code': 'DEU', 'flag': 'https://crests.football-data.org/759.svg'}, 'id': 2, 'name': 'TSG 1899 Hoffenheim', 'shortName': 'Hoffenheim', 'tla': 'TSG', 'crest': 'https://crests.football-data.org/2.png', 'address': 'Horrenberger Straße 58 Zuzenhausen 74939', 'website': 'http://www.achtzehn99.de', 'founded': 1921, 'clubColors': 'Blue / White', 'venue': 'PreZero Arena', 'runningCompetitions': [{'id': 2011, 'name': 'DFB-Pokal', 'code': 'DFB', 'type': 'CUP', 'emblem': 'https://crests.football-data.org/DFB_CUP.png'}, {'id': 2002, 'name': 'Bundesliga', 'code': 'BL1', 'type': 'LEAGUE', 'emblem': 'https://crests.footbal

In [ ]:
# Extract players
# This will be put in a separate script because of how long it takes to run (approximately 14 hours)

# The logic behind this script is the following: limited to 10 calls per minute with more than 250 000 players to extract from
# the API, I would need 20 days to extract all players. Therefore, we will only extract the players we might actually need, which 
# are the players from the 12 major leagues.
# To do so, we will follow 3 steps : 
    # 1) Export the 'players' table from the database
    # 2) Extract the players
    # 3) Load them in the database

# Step 1) Export the 'players' table
database_path = "C:/Users/mbmbm/matbx-data/sports-db-project/duckdb-databases/sports_db.duckdb"
with duckdb.connect(database_path) as con:
    all_players = con.sql('SELECT DISTINCT CAST(source_player_id AS INTEGER) AS player_id FROM dev.stg_football_data__players').df()
    all_players = all_players['player_id'].sort_values().to_list()

# Splitting the lists into lists of 100 items, to make debugging easier if an error occurs during extraction
# a) First, let's count the number of lists needed :
number_of_lists = len(all_players)//100 + 1

# b) Then, let's split the all_players list into {number_of_lists} lists
i = 0
all_players_lists = {}
while i <= number_of_lists:
    start_index = i*100
    end_index = 100*(i + 1)
    all_players_lists[i] = all_players[start_index:end_index]
    i = i + 1
    
# Step 2) Extract the players from the api

# Initialization
players_list = []
start_time = time.time() # I want to take a look at how long the extraction is
error_count = 0

for index, players_ids_group in all_players_lists.items():


    secrets=toml.load("C:/Users/mbmbm/matbx-data/sports-db-project/sports_db_pipeline/secrets.toml")
    request_header=secrets['source']['football_data']['request_header']
    api_key=secrets['source']['football_data']['api_key']

    information_to_extract = [
        'id', 
        'name',
        'firstName',
        'lastName', 
        'dateOfBirth', 
        'nationality', 
        'section', 
        'position', 
        'shirtNumber', 
        'lastUpdated', 
    ]
    i = 0

    for player_id in players_ids_group:
        i = i + 1
        try:
            url = f"https://api.football-data.org/v4/persons/{player_id}"
            response = requests.get(url, headers={request_header:api_key}).json()
            
            # Extract only wanted information thanks to dict comprehension. Also, we add two columns that were nested inside the json output
            dict_player = {key:value for (key,value) in response.items() if key in (information_to_extract)}
            dict_player['current_team_id'] = response['currentTeam']['id']
            dict_player['player_contract'] = response['currentTeam']['contract']
            # Adding the item to the players_list
            players_list.append(dict_player)
            if i%10 == 0: time.sleep(62)

        # If error, return and continue the loop:
        except:
            error_count = error_count + 1
            print("Group n°:", index)
            print("An error occured during this group's extraction")
            print(f"Error occurred around item {i} of the group")
            continue


df_players = pd.DataFrame(players_list)
with duckdb.connect(database_path) as con:
    con.sql('CREATE OR REPLACE TABLE raw.football_data__players AS SELECT * FROM df_players')

end_time = time.time()
extraction_time = end_time - start_time
print("The program ran for", extraction_time, "seconds with", error_count, "errors.")


Group n°: 51
An error occured during this group's extraction
Error occurred around item 56 of the group
Group n°: 79
An error occured during this group's extraction
Error occurred around item 6 of the group
The program ran for 50387.91194152832 seconds with 2 errors.


In [4]:
# The 2 players we're missing are 276641 & 179400 because they seem to not have a team currently
url = f"https://api.football-data.org/v4/persons/276641"
response2 = requests.get(url, headers={request_header:api_key}).json()
print(response2)

{'id': 276641, 'name': 'Brandon Powell', 'firstName': 'Brandon', 'lastName': 'Powell', 'dateOfBirth': '2005-10-17', 'nationality': 'England', 'section': 'Defence', 'position': None, 'shirtNumber': None, 'lastUpdated': '2025-03-09T09:42:43Z'}


In [ ]:
!jupyter nbconvert --to script football_data_pipeline_notebook_version.ipynb

[NbConvertApp] Converting notebook football_data_pipeline_notebook_version.ipynb to script
[NbConvertApp] Writing 10742 bytes to football_data_pipeline_notebook_version.py


: 